lecture3中是使用了一个mlp进行预测，并且使用前三个来预测下一个，在这里讲了过拟合、欠拟合、交叉熵、以及词嵌入方式，还有如何跟踪学习率，以及小批量训练方法，收获还是挺多的

一、数据集：
    因为要采用前三个来预测下一个，因此采用滑动窗口的方式，block_size=3，context=[0] * block_size，而后context[1:] +[ix]，每一个context作为一个样本。
二、过拟合、欠拟合：
    采用训练集、验证集、测试集进行对比，当loss_tr 与 loss_dev差不多的时候就是欠拟合，差很多就是过拟合
三、词嵌入方式：
    这里采用的是和上节课差不多的原理，但是效果更好，用的是pytorch的索引
四、跟踪学习率：
    先试出范围，然后用对数的方式来跟踪
五、总结
    这门课，新学习到的并不多，但是让我基础更好了！！！
    文档很重要，原理也很重要

In [2]:
import torch
import torch.nn.functional as F
import matplotlib.pyplot as plt
%matplotlib inline

In [3]:
words = open('names.txt', 'r').read().splitlines()

In [4]:
charts = sorted(list(set(''.join(words))))  # 字符集
stoi = {s: i for i, s in enumerate(charts)} 
stoi['.'] = 0
itos = {i:s for s,i in stoi.items()}


In [5]:
# building the dataset  用前三个来预测后一个
def build_dataset(words):
    block_size = 3 #使用滑动窗口的思想
    X, Y = [], []
    for w in words:
        print(w)
        context = [0] * block_size  #【0 0 0】
        for ch in w + '.': # 末尾加一个结束符号
            ix = stoi[ch]
            X.append(context)
            Y.append(ix)
            print(''.join(itos[i] for i in context), '->', itos[ix])
            context = context[1:] + [ix] # 滑动窗口，前面三个字符作为输入，最后一个字符作为输出
    X = torch.tensor(X)
    Y = torch.tensor(Y)
    return X, Y

In [ ]:
# C = torch.randn((27, 2)) # 27个字符，2维向量表示
# C[X].shape # 样本2维向量表示,对于X[]都需要进行词嵌入，pytorch支持直接按X的shape进行索引

torch.Size([32, 3, 2])

In [ ]:
# emb = C[X] # 词嵌入
# W1 = torch.randn((6,100)) # 6*100的矩阵，6是输入的维度，100是隐藏层的维度
# b = torch.randn(100) # 偏置项
# #这里不能直接emb @ W1 + b，因为emb的shape是(5, 3, 2)，而W1的shape是(6, 100)，所以需要reshape一下
# # reshape的方法有：  1.view和reshape，view是直接改变shape，reshape是先copy一份再改变shape，view会更快，因为它针对连续的内存块进行操作
# #                   2. 使用unbind结合cat，emb = torch.cat(torch.unbind(emb, dim=1), dim=1)  # 变成(5, 6)，然后再进行矩阵乘法
# h = emb.view(emb.shape[0], 6) @ W1 + b # 变成(5, 100)

In [6]:
g = torch.Generator().manual_seed(2147483647) # 随机数种子
C = torch.randn((27, 2), generator=g) # 27个字符，2维向量表示
W1 = torch.randn((6, 100), generator=g)
b1 = torch.randn(100, generator=g)
W2 = torch.randn((100, 27), generator=g)
b2 = torch.randn(27, generator=g)

parameters = [C, W1, b1, W2, b2] # 所有参数

In [7]:
sum(p.nelement() for p in parameters) # 计算参数的个数

3481

In [ ]:
# emb = C[X] # 词嵌入
# h = torch.tanh(emb.view(emb.shape[0],-1) @ W1 + b1)

# logits = h @ W2 +b2 # 计算输出(32, 27)
# counts = logits.exp()
# prob = counts / counts.sum(1, keepdim=True) # 计算概率分布
# loss = -prob[torch.arange(32),Y].log().mean()
# # print(loss)
# F.cross_entropy(logits, Y) # 交叉熵损失函数，和上面的loss是一样的
# # 交叉熵的话更好，因为首先采用聚类表达式更高效，其次不会出现inf的情况，
# #  如果采用exp那么可能出现x[.].exp超出范围的情况，而交叉熵会自动减去最大值，负数不会超范围且对数值无影响

tensor(18.8451)


tensor(18.8451)

In [8]:
for p in parameters:
    p.requires_grad = True

In [ ]:
# for _ in range(100):
# # 使用全部数据进行训练非常耗时，因此采用小批量数据
#     ix = torch.randint(0,X.shape[0],(32,)) #随机产生32个0-X.shape[0] 的值

#     #forward
#     emb = C[X[ix]] # (32,3,2)
#     h = torch.tanh(emb.view(emb.shape[0],-1) @ W1 + b1)
#     logits = h @ W2 + b2
#     loss = F.cross_entropy(logits,Y[ix])

#     #backward
#     for p in parameters:
#         p.grad = None
#     loss.backward()
#     #update
#     for p in parameters:
#         if p.grad is not None:
#             p.data += -0.1* p.grad
# print(loss.item())

2.669793128967285


In [9]:
emb = C[X] # (32,3,2)
h = torch.tanh(emb.view(emb.shape[0],-1) @ W1 + b1)
logits = h @ W2 + b2
print(logits.shape)
loss = F.cross_entropy(logits,Y)
loss
#模型小、数据集大，loss低很可能是过拟合---->训练集、测试集

NameError: name 'X' is not defined

In [10]:
#training spilt, validation spilt, test spilt
#80,              10,               10
import random
random.seed(42)
random.shuffle(words)
n1 = int(0.8*len(words))
n2 = int(0.9*len(words))

Xtr,Ytr = build_dataset(words[:n1])
Xdev,Ydev = build_dataset(words[n1:n2])
Xte,Yte = build_dataset(words[:n1])

yuheng
... -> y
..y -> u
.yu -> h
yuh -> e
uhe -> n
hen -> g
eng -> .
diondre
... -> d
..d -> i
.di -> o
dio -> n
ion -> d
ond -> r
ndr -> e
dre -> .
xavien
... -> x
..x -> .
.x. -> v
x.v -> i
.vi -> e
vie -> n
ien -> .
jori
... -> j
..j -> o
.jo -> r
jor -> i
ori -> .
juanluis
... -> j
..j -> u
.ju -> .
ju. -> n
u.n -> l
.nl -> u
nlu -> i
lui -> s
uis -> .
erandi
... -> e
..e -> r
.er -> .
er. -> n
r.n -> d
.nd -> i
ndi -> .
phia
... -> p
..p -> h
.ph -> i
phi -> .
hi. -> .
samatha
... -> s
..s -> .
.s. -> m
s.m -> .
.m. -> t
m.t -> h
.th -> .
th. -> .
phoenix
... -> p
..p -> h
.ph -> o
pho -> e
hoe -> n
oen -> i
eni -> x
nix -> .
emmelynn
... -> e
..e -> m
.em -> m
emm -> e
mme -> l
mel -> y
ely -> n
lyn -> n
ynn -> .
hollan
... -> h
..h -> o
.ho -> l
hol -> l
oll -> .
ll. -> n
l.n -> .
hollis
... -> h
..h -> o
.ho -> l
hol -> l
oll -> i
lli -> s
lis -> .
callalily
... -> c
..c -> .
.c. -> l
c.l -> l
.ll -> .
ll. -> l
l.l -> i
.li -> l
lil -> y
ily -> .
adelayde
... -> .
... -> d
..d

In [12]:
for _ in range(10):
# 使用全部数据进行训练非常耗时，因此采用小批量数据
    ix = torch.randint(0,Xtr.shape[0],(32,)) #随机产生32个0-X.shape[0] 的值

    #forward
    emb = C[Xtr[ix]] # (32,3,2)
    h = torch.tanh(emb.view(emb.shape[0],-1) @ W1 + b1)
    logits = h @ W2 + b2
    print(h.shape)
    loss = F.cross_entropy(logits,Ytr[ix])

    #backward
    for p in parameters:
        p.grad = None
    loss.backward()
    #update
    for p in parameters:
        if p.grad is not None:
            p.data += -0.01* p.grad

torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])
torch.Size([32, 100])


In [59]:
emb = C[Xtr] # (32, 3, 2)
h = torch.tanh(emb.view(-1, 6) @ W1 + b1) # (32, 100)
logits = h @ W2 + b2 # (32, 27)
loss = F.cross_entropy(logits, Ytr)
loss

tensor(2.2401, grad_fn=<NllLossBackward0>)

In [60]:
emb = C[Xdev] # (32, 3, 2)
h = torch.tanh(emb.view(-1, 6) @ W1 + b1) # (32, 100)
logits = h @ W2 + b2 # (32, 27)
loss = F.cross_entropy(logits, Ydev)
loss

tensor(2.2373, grad_fn=<NllLossBackward0>)

In [61]:
#在这里训练集和验证集的loss差不多，说明还在欠拟合，有两种可能：emb的空间太小，hidden太小
#因此可以扩大词向量空间，以及hidden大小，或者是提高batch
# 当train spilt 的loss 与 dev loss 相差很大时说明过拟合了，需要在过拟合前就停止！

In [62]:
context = [0] * 3
C[torch.tensor([context])].shape

torch.Size([1, 3, 2])

In [63]:

g = torch.Generator().manual_seed(2147483647 + 10)
for _ in range(20):

    out = []
    context = [0] * 3
    while True:
        emb = C[torch.tensor([context])]
        h = torch.tanh(emb.view(1, -1) @ W1 + b1)
        logits = h @ W2 + b2
        probs = F.softmax(logits, dim=1)
        ix = torch.multinomial(probs, num_samples=1, generator=g).item()
        context = context[1:] + [ix]
        out.append(ix)
        if ix == 0:
            break
    print(''.join(itos[i] for i in out))

desie.
yre.
.
ir.
lil.
nsi.
rui.
d.
ildorto.
k.
sion.
grie.
sid.
rhrij.
.
s.
nist.
dineisell.
ilo.
i.
